In [1]:




















import plotly.express as px
import plotly.graph_objects as go
from sklearn.model_selection import train_test_split
from sklearn.ensemble import RandomForestRegressor
from sklearn.metrics import mean_squared_error
import pickle
import numpy as np
import pandas as pd
from sklearn.impute import SimpleImputer
from sklearn.impute import KNNImputer

#### Read pickled dataframes and set timestamp as index (to allow later join)

In [2]:
df_verkehr_stjohann = pd.read_pickle("../data/clean/df_verkehr_stjohann.pkl")

In [3]:
df_verkehr_stjohann = df_verkehr_stjohann.set_index("timestamp")

In [4]:
df_basel_bin = pd.read_pickle("../data/clean/df_basel_bin.pkl")

In [5]:
df_basel_bin = df_basel_bin.set_index("timestamp")

In [6]:
df_basel_wetter = pd.read_pickle("../data/clean/df_basel_wetter.pkl")

In [7]:
df_basel_wetter = df_basel_wetter.set_index("timestamp")

In [8]:
df_basel_wetter.head()

temp  humidity  pressure  precipitation  cloudcover  \
timestamp                                                                      
2014-01-01 00:00:00  1.690529      45.0    1017.8            0.0        17.0   
2014-01-01 01:00:00  2.080528      41.0    1018.1            0.0       100.0   
2014-01-01 02:00:00  2.130529      39.0    1018.0            0.0       100.0   
2014-01-01 03:00:00  3.320529      42.0    1017.2            0.0       100.0   
2014-01-01 04:00:00  5.190528      56.0    1016.3            0.0       100.0   

                     sunshine_duration  shortwave_radiation  wind_speed  \
timestamp                                                                 
2014-01-01 00:00:00                0.0                  0.0    5.145039   
2014-01-01 01:00:00                0.0                  0.0    5.491976   
2014-01-01 02:00:00                0.0                  0.0    5.361196   
2014-01-01 03:00:00                0.0                  0.0    4.144211   
2014-01-01 04:00:00                0.0                  0.0    3.463200   

                     wind_direction  
timestamp                            
2014-01-01 00:00:00       111.25050  
2014-01-01 01:00:00       104.03624  
2014-01-01 02:00:00       116.56505  
2014-01-01 03:00:00       135.00000  
2014-01-01 04:00:00       180.00000

In [9]:
df_basel_bin.head()

O3   NO2  SO2  PM10  PM2.5   EC      CPC   NOX  TEMP  \
timestamp                                                                    
2014-01-01 01:00:00  7.1  36.7  5.3  35.6    NaN  1.4  17257.8  43.2   0.5   
2014-01-01 02:00:00  4.7  35.5  6.3  57.3    NaN  1.5  20101.9  47.1   0.3   
2014-01-01 03:00:00  3.1  33.9  3.9  69.1    NaN  1.3  14095.9  42.4   0.2   
2014-01-01 04:00:00  1.9  33.8  3.2  48.4    NaN  1.3  13157.1  45.8   0.2   
2014-01-01 05:00:00  2.7  33.5  2.8  41.6    NaN  1.2  11711.8  41.0   0.6   

                     PREC  RAD  
timestamp                       
2014-01-01 01:00:00   0.0  0.0  
2014-01-01 02:00:00   0.0  0.0  
2014-01-01 03:00:00   0.0  0.0  
2014-01-01 04:00:00   0.1  0.0  
2014-01-01 05:00:00   0.0  0.0

In [10]:
df_verkehr_stjohann.head()

SiteCode                           SiteName  \
timestamp                                                          
2014-08-12 01:00:00       660  660 Flughafenstrasse, Grenze CH-F   
2014-08-12 02:00:00       660  660 Flughafenstrasse, Grenze CH-F   
2014-08-12 03:00:00       660  660 Flughafenstrasse, Grenze CH-F   
2014-08-12 04:00:00       660  660 Flughafenstrasse, Grenze CH-F   
2014-08-12 05:00:00       660  660 Flughafenstrasse, Grenze CH-F   

                                         DirectionName  LaneCode LaneName  \
timestamp                                                                   
2014-08-12 01:00:00  1 von Flughafen (1 FS mit ÖV-Bus)         1   Spur 1   
2014-08-12 02:00:00  1 von Flughafen (1 FS mit ÖV-Bus)         1   Spur 1   
2014-08-12 03:00:00  1 von Flughafen (1 FS mit ÖV-Bus)         1   Spur 1   
2014-08-12 04:00:00  1 von Flughafen (1 FS mit ÖV-Bus)         1   Spur 1   
2014-08-12 05:00:00  1 von Flughafen (1 FS mit ÖV-Bus)         1   Spur 1   

                           Date TimeFrom TimeTo  ValuesApproved  ValuesEdited  \
timestamp                                                                       
2014-08-12 01:00:00  12.08.2014    00:00  01:00               1             1   
2014-08-12 02:00:00  12.08.2014    01:00  02:00               1             1   
2014-08-12 03:00:00  12.08.2014    02:00  03:00               1             1   
2014-08-12 04:00:00  12.08.2014    03:00  04:00               1             1   
2014-08-12 05:00:00  12.08.2014    04:00  05:00               1             1   

                      ...    PW  PW+  Lief  Lief+  Lief+Aufl.  LW  LW+  \
timestamp             ...                                                
2014-08-12 01:00:00   ...    42    0     2      0           0   0    0   
2014-08-12 02:00:00   ...     2    0     1      0           0   0    0   
2014-08-12 03:00:00   ...     5    0     0      0           0   0    0   
2014-08-12 04:00:00   ...    13    0     4      0           0   0    0   
2014-08-12 05:00:00   ...    48    0     6      0           0   2    0   

                     Sattelzug  Bus  andere  
timestamp                                    
2014-08-12 01:00:00          0    3       0  
2014-08-12 02:00:00          0    0       0  
2014-08-12 03:00:00          0    0       0  
2014-08-12 04:00:00          0    0       0  
2014-08-12 05:00:00          0    1       0  

[5 rows x 23 columns]

#### Issue: All three dataframes have different starting timestamps. Only merge data within common timestamp range

In [11]:
[df_verkehr_stjohann.index.max(), df_basel_bin.index.max(), df_basel_wetter.index.max()]

[Timestamp('2020-05-04 23:00:00'),
 Timestamp('2020-05-04 00:00:00'),
 Timestamp('2020-05-03 23:00:00')]

In [12]:
[df_verkehr_stjohann.index.min(), df_basel_bin.index.min(), df_basel_wetter.index.min()]

[Timestamp('2014-08-12 00:00:00'),
 Timestamp('2014-01-01 01:00:00'),
 Timestamp('2014-01-01 00:00:00')]

#### Check if columns with same names exist before merging dataframes

In [13]:
df_basel_wetter.columns

Index(['temp', 'humidity', 'pressure', 'precipitation', 'cloudcover',
       'sunshine_duration', 'shortwave_radiation', 'wind_speed',
       'wind_direction'],
      dtype='object')

In [14]:
df_basel_bin.columns

Index(['O3', 'NO2', 'SO2', 'PM10', 'PM2.5', 'EC', 'CPC', 'NOX', 'TEMP', 'PREC',
       'RAD'],
      dtype='object')

In [15]:
df_basel_wetter.shape

(55560, 9)

In [16]:
df_basel_bin.shape

(55560, 11)

In [17]:
df_verkehr_stjohann.shape

(97632, 23)

In [18]:
df_verkehr_stjohann.loc['01.01.2016']

SiteCode                           SiteName  \
timestamp                                                          
2016-01-01 01:00:00       660  660 Flughafenstrasse, Grenze CH-F   
2016-01-01 02:00:00       660  660 Flughafenstrasse, Grenze CH-F   
2016-01-01 03:00:00       660  660 Flughafenstrasse, Grenze CH-F   
2016-01-01 04:00:00       660  660 Flughafenstrasse, Grenze CH-F   
2016-01-01 05:00:00       660  660 Flughafenstrasse, Grenze CH-F   
2016-01-01 06:00:00       660  660 Flughafenstrasse, Grenze CH-F   
2016-01-01 07:00:00       660  660 Flughafenstrasse, Grenze CH-F   
2016-01-01 08:00:00       660  660 Flughafenstrasse, Grenze CH-F   
2016-01-01 09:00:00       660  660 Flughafenstrasse, Grenze CH-F   
2016-01-01 10:00:00       660  660 Flughafenstrasse, Grenze CH-F   
2016-01-01 11:00:00       660  660 Flughafenstrasse, Grenze CH-F   
2016-01-01 12:00:00       660  660 Flughafenstrasse, Grenze CH-F   
2016-01-01 13:00:00       660  660 Flughafenstrasse, Grenze CH-F   
2016-01-01 14:00:00       660  660 Flughafenstrasse, Grenze CH-F   
2016-01-01 15:00:00       660  660 Flughafenstrasse, Grenze CH-F   
2016-01-01 16:00:00       660  660 Flughafenstrasse, Grenze CH-F   
2016-01-01 17:00:00       660  660 Flughafenstrasse, Grenze CH-F   
2016-01-01 18:00:00       660  660 Flughafenstrasse, Grenze CH-F   
2016-01-01 19:00:00       660  660 Flughafenstrasse, Grenze CH-F   
2016-01-01 20:00:00       660  660 Flughafenstrasse, Grenze CH-F   
2016-01-01 21:00:00       660  660 Flughafenstrasse, Grenze CH-F   
2016-01-01 22:00:00       660  660 Flughafenstrasse, Grenze CH-F   
2016-01-01 23:00:00       660  660 Flughafenstrasse, Grenze CH-F   
2016-01-01 00:00:00       660  660 Flughafenstrasse, Grenze CH-F   
2016-01-01 01:00:00       660  660 Flughafenstrasse, Grenze CH-F   
2016-01-01 02:00:00       660  660 Flughafenstrasse, Grenze CH-F   
2016-01-01 03:00:00       660  660 Flughafenstrasse, Grenze CH-F   
2016-01-01 04:00:00       660  660 Flughafenstrasse, Grenze CH-F   
2016-01-01 05:00:00       660  660 Flughafenstrasse, Grenze CH-F   
2016-01-01 06:00:00       660  660 Flughafenstrasse, Grenze CH-F   
2016-01-01 07:00:00       660  660 Flughafenstrasse, Grenze CH-F   
2016-01-01 08:00:00       660  660 Flughafenstrasse, Grenze CH-F   
2016-01-01 09:00:00       660  660 Flughafenstrasse, Grenze CH-F   
2016-01-01 10:00:00       660  660 Flughafenstrasse, Grenze CH-F   
2016-01-01 11:00:00       660  660 Flughafenstrasse, Grenze CH-F   
2016-01-01 12:00:00       660  660 Flughafenstrasse, Grenze CH-F   
2016-01-01 13:00:00       660  660 Flughafenstrasse, Grenze CH-F   
2016-01-01 14:00:00       660  660 Flughafenstrasse, Grenze CH-F   
2016-01-01 15:00:00       660  660 Flughafenstrasse, Grenze CH-F   
2016-01-01 16:00:00       660  660 Flughafenstrasse, Grenze CH-F   
2016-01-01 17:00:00       660  660 Flughafenstrasse, Grenze CH-F   
2016-01-01 18:00:00       660  660 Flughafenstrasse, Grenze CH-F   
2016-01-01 19:00:00       660  660 Flughafenstrasse, Grenze CH-F   
2016-01-01 20:00:00       660  660 Flughafenstrasse, Grenze CH-F   
2016-01-01 21:00:00       660  660 Flughafenstrasse, Grenze CH-F   
2016-01-01 22:00:00       660  660 Flughafenstrasse, Grenze CH-F   
2016-01-01 23:00:00       660  660 Flughafenstrasse, Grenze CH-F   
2016-01-01 00:00:00       660  660 Flughafenstrasse, Grenze CH-F   

                                          DirectionName  LaneCode LaneName  \
timestamp                                                                    
2016-01-01 01:00:00   1 von Flughafen (1 FS mit ÖV-Bus)         1   Spur 1   
2016-01-01 02:00:00   1 von Flughafen (1 FS mit ÖV-Bus)         1   Spur 1   
2016-01-01 03:00:00   1 von Flughafen (1 FS mit ÖV-Bus)         1   Spur 1   
2016-01-01 04:00:00   1 von Flughafen (1 FS mit ÖV-Bus)         1   Spur 1   
2016-01-01 05:00:00   1 von Flughafen (1 FS mit ÖV-Bus)         1   Spur 1   
2016-01-01 06:00:00   1 von Flughafen (1 FS mit ÖV-Bus)         1   Spur 1

#### traffic data has two lanes (Spur 1, Spur 2)

In [19]:
df_verkehr_stjohann[df_verkehr_stjohann.LaneName == "Spur 1"].loc['2014-01-01 01:00:00' : '2020-05-03 23:00:00'].Total

timestamp
2014-08-12 01:00:00     48
2014-08-12 02:00:00      3
2014-08-12 03:00:00      6
2014-08-12 04:00:00     17
2014-08-12 05:00:00     57
2014-08-12 06:00:00    176
2014-08-12 07:00:00    119
2014-08-12 08:00:00    100
2014-08-12 09:00:00    140
2014-08-12 10:00:00    139
2014-08-12 11:00:00    214
2014-08-12 12:00:00    345
2014-08-12 13:00:00    262
2014-08-12 14:00:00    181
2014-08-12 15:00:00    207
2014-08-12 16:00:00    255
2014-08-12 17:00:00    468
2014-08-12 18:00:00    575
2014-08-12 19:00:00    459
2014-08-12 20:00:00    258
2014-08-12 21:00:00    193
2014-08-12 22:00:00    220
2014-08-12 23:00:00    239
2014-08-12 00:00:00    328
2014-08-13 01:00:00     62
2014-08-13 02:00:00     13
2014-08-13 03:00:00      4
2014-08-13 04:00:00     17
2014-08-13 05:00:00     96
2014-08-13 06:00:00    141
                      ... 
2020-05-02 19:00:00     15
2020-05-02 20:00:00     14
2020-05-02 21:00:00     15
2020-05-02 22:00:00     16
2020-05-02 23:00:00     12
2020-05-02 00:00:0

In [20]:
df_basel_bin.loc['2014-01-01 01:00:00' : '2020-05-03 23:00:00'].shape

(55559, 11)

In [21]:
df_basel_wetter.loc['2014-01-01 01:00:00' : '2020-05-03 23:00:00'].shape

(55559, 9)

#### join dataframes (inner, only keep those where the same index exists in every dataframe)

In [22]:
df_all = df_basel_bin.join(df_verkehr_stjohann[df_verkehr_stjohann.LaneName == "Spur 1"].Total, how="inner")

#### Reorganize dataframe. Instead of a column LaneName and Total Traffic, Change to a TrafficIn and TrafficOut column

In [23]:
df_all.rename(columns={'Total':'TrafficIn'}, inplace=True)

In [24]:
df_all.head()

O3   NO2  SO2  PM10  PM2.5   EC     CPC   NOX  TEMP  \
timestamp                                                                    
2014-08-12 00:00:00  47.7   4.4  0.3   7.6    NaN  0.1  3616.1   4.6  14.6   
2014-08-12 01:00:00  44.7   5.7  0.4   8.4    NaN  0.1  4250.2   5.9  14.6   
2014-08-12 02:00:00  37.5  10.2  0.5   9.6    NaN  0.2  5239.0  10.5  14.3   
2014-08-12 03:00:00  25.4  15.5  1.0  14.6    NaN  0.2  7199.5  15.9  13.6   
2014-08-12 04:00:00  25.5  11.8  0.9  12.6    NaN  0.4  6644.1  12.2  13.6   

                     PREC  RAD  TrafficIn  
timestamp                                  
2014-08-12 00:00:00   0.0  0.0        328  
2014-08-12 01:00:00   0.0  0.0         48  
2014-08-12 02:00:00   0.0  0.0          3  
2014-08-12 03:00:00   0.0  0.0          6  
2014-08-12 04:00:00   0.0  0.0         17

In [25]:
df_all = df_all.join(df_verkehr_stjohann[df_verkehr_stjohann.LaneName == "Spur 2"].Total, how="inner")

In [26]:
df_all.rename(columns={'Total':'TrafficOut'}, inplace=True)

In [27]:
df_all = df_all.join(df_basel_wetter, how="inner")

#### Drop weather data columns from air pollution data frame, so only one temperature/precipitation/radiation is used

In [28]:
df_all = df_all.drop(["TEMP", "PREC", "RAD"], axis=1)

In [29]:
df_all.head()

O3   NO2  SO2  PM10  PM2.5   EC     CPC   NOX  \
timestamp                                                              
2014-08-12 00:00:00  47.7   4.4  0.3   7.6    NaN  0.1  3616.1   4.6   
2014-08-12 01:00:00  44.7   5.7  0.4   8.4    NaN  0.1  4250.2   5.9   
2014-08-12 02:00:00  37.5  10.2  0.5   9.6    NaN  0.2  5239.0  10.5   
2014-08-12 03:00:00  25.4  15.5  1.0  14.6    NaN  0.2  7199.5  15.9   
2014-08-12 04:00:00  25.5  11.8  0.9  12.6    NaN  0.4  6644.1  12.2   

                     TrafficIn  TrafficOut       temp  humidity  pressure  \
timestamp                                                                   
2014-08-12 00:00:00        328          56  18.010529      57.0    1015.4   
2014-08-12 01:00:00         48          12  17.760529      56.0    1015.8   
2014-08-12 02:00:00          3           2  17.550530      57.0    1016.0   
2014-08-12 03:00:00          6           6  17.430529      60.0    1015.6   
2014-08-12 04:00:00         17          28  17.040530      64.0    1015.2   

                     precipitation  cloudcover  sunshine_duration  \
timestamp                                                           
2014-08-12 00:00:00            0.0       100.0                0.0   
2014-08-12 01:00:00            0.0       100.0                0.0   
2014-08-12 02:00:00            0.0       100.0                0.0   
2014-08-12 03:00:00            0.0       100.0                0.0   
2014-08-12 04:00:00            0.0       100.0                0.0   

                     shortwave_radiation  wind_speed  wind_direction  
timestamp                                                             
2014-08-12 00:00:00                  0.0    5.394189       200.22485  
2014-08-12 01:00:00                  0.0    2.513213       237.99463  
2014-08-12 02:00:00                  0.0    2.781298       196.69925  
2014-08-12 03:00:00                  0.0    2.623736       203.96250  
2014-08-12 04:00:00                  0.0    3.996000       216.86990

#### Look if values for air pollution contain na values

In [30]:
df_all['PM2.5'].isna().value_counts()

False    36810
True     11982
Name: PM2.5, dtype: int64

In [31]:
df_all['PM10'].isna().value_counts()

False    46457
True      2335
Name: PM10, dtype: int64

In [32]:
df_all['O3'].isna().value_counts()

False    48522
True       270
Name: O3, dtype: int64

In [33]:
df_all['EC'].isna().value_counts()

False    48518
True       274
Name: EC, dtype: int64

In [34]:
df_all['CPC'].isna().value_counts()

False    48699
True        93
Name: CPC, dtype: int64

In [35]:
df_all['NOX'].isna().value_counts()

False    48536
True       256
Name: NOX, dtype: int64

#### It seems that values are missing.
#### We tried to use a KNNImputer for the missing values, but python kernel crashed. Problem is probably that missing data are in periods where sensors were defective, so KNNImputer does not work properly. Instead we decided to just skip all dataframe rows were values of air pollution data is missing

In [36]:
#nominal_columns_missing = df_all.columns[0:8]

In [37]:
#impute_missing=KNNImputer()

In [38]:
#df_all['NOX'].reset_index()

In [39]:
#impute_missing.fit_transform([df_all['PM2.5']]).shape

In [40]:
#nominal_columns_missing

In [41]:
#np.squeeze(impute_missing.fit_transform([df_all['O3']])).shape

In [42]:
#df_all['O3'].shape

In [43]:
#for col in nominal_columns_missing:
#    print(col)
#    df_all[col] = np.squeeze(impute_missing.fit_transform([df_all['O3']]))

In [44]:
#df_all['NOX'].isna().value_counts()


#### Disassemble timestamp into hour, weekday, month, year and day for later modelling and put this in seperate columns

In [45]:
df_all['hour'] = df_all.index.hour

In [46]:
df_all['weekday'] = df_all.index.weekday

In [47]:
df_all['month'] = df_all.index.month

In [48]:
df_all['year'] = df_all.index.year

In [49]:
df_all['day'] = df_all.index.day

#### look at sample data and pickle it

In [50]:
df_all.sample(n=20)

O3   NO2  SO2  PM10  PM2.5   EC      CPC    NOX  \
timestamp                                                                
2015-07-23 16:00:00  87.0  14.3  0.3  15.7    NaN  0.5   8089.3   15.7   
2016-01-16 03:00:00  51.3   6.0  0.2   3.4    2.9  0.2   2546.2    5.8   
2014-11-28 03:00:00   0.4  30.8  0.3  11.8    NaN  0.7   1829.8   41.7   
2017-03-20 19:00:00  63.2  10.0  0.4   3.0    1.1  0.1   7439.5   10.9   
2020-01-09 19:00:00   8.2  57.5  2.3   NaN   14.3  0.8  14191.9   61.8   
2017-12-04 22:00:00   1.6  55.5  5.3  25.9   20.0  1.4  16542.0  104.0   
2017-10-23 02:00:00  67.1   1.4  0.3   5.1    2.6  0.1   2209.9    1.3   
2018-03-10 21:00:00  42.4  23.4  1.6  14.2   11.2  0.6   8502.6   24.2   
2018-05-17 22:00:00  64.7   8.2  0.4  11.5   10.9  0.2   5717.8    8.6   
2018-03-14 06:00:00  64.0   8.2  0.7   2.8    2.4  0.1   4112.3    8.6   
2017-01-24 10:00:00  19.2  52.9  1.4  49.6   45.0  1.5   7606.3   60.5   
2016-01-02 00:00:00  42.5  10.7  0.9  11.9    9.9  0.3   3603.9   11.2   
2019-08-17 10:00:00  31.9  19.5  2.4  11.9    7.4  0.4  18845.0   30.2   
2018-08-22 06:00:00  51.7  23.4  6.1  14.4   12.0  0.4  10922.5   24.2   
2017-11-01 17:00:00  10.4  45.6  3.0  29.7   15.9  1.0  14657.6   63.9   
2019-10-06 00:00:00  16.7  16.0  0.3   NaN   12.8  0.4   6329.3   16.6   
2016-03-26 16:00:00  88.4   6.0  0.4   4.7    4.6  0.2   7365.3    7.1   
2017-03-08 07:00:00  24.4  31.1  1.9   6.2    3.5  0.5  11898.2   35.4   
2014-12-31 20:00:00   4.4  54.2  4.3  43.4   37.9  2.2  22688.1   78.1   
2015-09-26 17:00:00  67.3  12.6  0.4   9.2    NaN  0.3   8933.9   13.4   

                     TrafficIn  TrafficOut ...   cloudcover  \
timestamp                                  ...                
2015-07-23 16:00:00        383         340 ...        100.0   
2016-01-16 03:00:00          7           6 ...        100.0   
2014-11-28 03:00:00          8           7 ...        100.0   
2017-03-20 19:00:00        332         152 ...        100.0   
2020-01-09 19:00:00        329         200 ...          5.4   
2017-12-04 22:00:00        249         169 ...        100.0   
2017-10-23 02:00:00          1           1 ...        100.0   
2018-03-10 21:00:00         92          97 ...        100.0   
2018-05-17 22:00:00        137         102 ...          7.0   
2018-03-14 06:00:00        158         338 ...         16.0   
2017-01-24 10:00:00        210         277 ...        100.0   
2016-01-02 00:00:00        239          50 ...         55.0   
2019-08-17 10:00:00        324         345 ...        100.0   
2018-08-22 06:00:00        133         214 ...          0.0   
2017-11-01 17:00:00        438         270 ...          2.4   
2019-10-06 00:00:00        440         129 ...        100.0   
2016-03-26 16:00:00        183         214 ...          0.0   
2017-03-08 07:00:00        151         330 ...         23.0   
2014-12-31 20:00:00         90         134 ...          0.0   
2015-09-26 17:00:00        286         242 ...         10.0   

                     sunshine_duration  shortwave_radiation  wind_speed  \
timestamp                                                                 
2015-07-23 16:00:00           0.000000           413.850000    9.899905   
2016-01-16 03:00:00           0.000000             0.000000   15.533656   
2014-11-28 03:00:00           0.000000             0.000000    8.578741   
2017-03-20 19:00:00           0.000000            33.820000   11.131568   
2020-01-09 19:00:00           0.000000             0.000000    8.819409   
2017-12-04 22:00:00           0.000000             0.000000   10.042255   
2017-10-23 02:00:00           0.000000             0.000000   13.906487   
2018-03-10 21:00:00           0.000000             0.000000    7.983115   
2018-05-17 22:00:00           0.000000             0.000000    7.173039   
2018-03-14 06:00:00           0.000000             0.000000    5.663742   
2017-01-24 10:00:00           0.000000           168.209990    3.554219   
2016-01-02 00:00:00           0.

In [51]:
df_all = df_all.reset_index()

In [52]:
df_all.to_pickle("../data/clean/df_all.pkl")

#### start modelling, only use subset without nan, start with ozone (O3)

In [53]:
df_all_clean = df_all[df_all['O3'].isna() == False]

In [54]:
categorical_columns = ["hour", "weekday", "month", "year", "day"]

#### do one-hot encoding, create X and y data (X is weather, traffic and timestamp, y is ozone concentration)

In [55]:
for col in categorical_columns:
    df_all_clean[col] = df_all_clean[col].astype('category')

/usr/lib/python3/dist-packages/ipykernel_launcher.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  


In [56]:
df = pd.get_dummies(df_all_clean, drop_first=True)

In [57]:
df.head()

timestamp    O3   NO2  SO2  PM10  PM2.5   EC     CPC   NOX  \
0 2014-08-12 00:00:00  47.7   4.4  0.3   7.6    NaN  0.1  3616.1   4.6   
1 2014-08-12 01:00:00  44.7   5.7  0.4   8.4    NaN  0.1  4250.2   5.9   
2 2014-08-12 02:00:00  37.5  10.2  0.5   9.6    NaN  0.2  5239.0  10.5   
3 2014-08-12 03:00:00  25.4  15.5  1.0  14.6    NaN  0.2  7199.5  15.9   
4 2014-08-12 04:00:00  25.5  11.8  0.9  12.6    NaN  0.4  6644.1  12.2   

   TrafficIn   ...    day_22  day_23  day_24  day_25  day_26  day_27  day_28  \
0        328   ...         0       0       0       0       0       0       0   
1         48   ...         0       0       0       0       0       0       0   
2          3   ...         0       0       0       0       0       0       0   
3          6   ...         0       0       0       0       0       0       0   
4         17   ...         0       0       0       0       0       0       0   

   day_29  day_30  day_31  
0       0       0       0  
1       0       0       0  
2       0       0       0  
3       0       0       0  
4       0       0       0  

[5 rows x 96 columns]

In [58]:
X = df[df.columns[9:]]

In [59]:
y = df['O3']

In [60]:
X.head()

TrafficIn  TrafficOut       temp  humidity  pressure  precipitation  \
0        328          56  18.010529      57.0    1015.4            0.0   
1         48          12  17.760529      56.0    1015.8            0.0   
2          3           2  17.550530      57.0    1016.0            0.0   
3          6           6  17.430529      60.0    1015.6            0.0   
4         17          28  17.040530      64.0    1015.2            0.0   

   cloudcover  sunshine_duration  shortwave_radiation  wind_speed   ...    \
0       100.0                0.0                  0.0    5.394189   ...     
1       100.0                0.0                  0.0    2.513213   ...     
2       100.0                0.0                  0.0    2.781298   ...     
3       100.0                0.0                  0.0    2.623736   ...     
4       100.0                0.0                  0.0    3.996000   ...     

   day_22  day_23  day_24  day_25  day_26  day_27  day_28  day_29  day_30  \
0       0       0       0       0       0       0       0       0       0   
1       0       0       0       0       0       0       0       0       0   
2       0       0       0       0       0       0       0       0       0   
3       0       0       0       0       0       0       0       0       0   
4       0       0       0       0       0       0       0       0       0   

   day_31  
0       0  
1       0  
2       0  
3       0  
4       0  

[5 rows x 87 columns]

In [61]:
y.head()

0    47.7
1    44.7
2    37.5
3    25.4
4    25.5
Name: O3, dtype: float64

In [62]:
y.isna().value_counts()

False    48522
Name: O3, dtype: int64

#### Try first a multi layer perceptron for modelling

In [63]:
from sklearn.neural_network import MLPRegressor

In [64]:
mlp = MLPRegressor()

#### train test split

In [65]:
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.33, random_state=42)

In [66]:
mlp.fit(X_train, y_train)

MLPRegressor(activation='relu', alpha=0.0001, batch_size='auto', beta_1=0.9,
             beta_2=0.999, early_stopping=False, epsilon=1e-08,
             hidden_layer_sizes=(100,), learning_rate='constant',
             learning_rate_init=0.001, max_fun=15000, max_iter=200,
             momentum=0.9, n_iter_no_change=10, nesterovs_momentum=True,
             power_t=0.5, random_state=None, shuffle=True, solver='adam',
             tol=0.0001, validation_fraction=0.1, verbose=False,
             warm_start=False)

In [67]:
from sklearn.metrics import r2_score
y_predmlp = mlp.predict(X_test)
r2_score(y_test, y_predmlp)

0.7699379857533799

In [68]:
y_predmlp

array([-3.85928694, 67.26047252, 92.72150261, ..., 45.36339089,
       12.04113797, 63.65707767])

In [69]:
df_mlp_plot1 = pd.DataFrame(data=mlp.predict(X), index=df.timestamp, columns={'value'})

In [70]:
df_mlp_plot1['type'] = 'Prediction'

In [71]:
df_mlp_plot2 = pd.DataFrame()

In [72]:
df_mlp_plot2['value'] = y

In [73]:
df_mlp_plot2.index = df.timestamp

In [74]:
df_mlp_plot2['type'] = 'Data'

In [75]:
df_mlp_plot = pd.concat([df_mlp_plot1, df_mlp_plot2])

In [76]:
df_mlp_plot = df_mlp_plot.sort_values('timestamp')

In [77]:
px.line(x=df_mlp_plot.index[0:500], y=df_mlp_plot.value[0:500], color=df_mlp_plot.type[0:500], color_discrete_sequence=["darkgreen", "yellow"]) 

#### Now a linear model

In [78]:
from sklearn import linear_model

In [79]:
lm = linear_model.LinearRegression()

In [80]:
lm.fit(X_train, y_train)

LinearRegression(copy_X=True, fit_intercept=True, n_jobs=None, normalize=False)

In [81]:
y_predlm = lm.predict(X_test)
r2_score(y_test, y_predlm)

0.6543257157570724

px.line(x=df.timestamp[0:100], y=lm.predict(X)[0:100], color_discrete_sequence=["darkgreen"])

#### Now a Stochastic gradient regressor

In [82]:
from sklearn.linear_model import SGDRegressor #Stochastic Gradiant Regressor

In [83]:
sgd = SGDRegressor(verbose=True)

In [84]:
sgd.fit(X_train, y_train)

-- Epoch 1
Norm: 1886943399480.70, NNZs: 87, Bias: 599648461.860748, T: 32509, Avg. loss: 332597854823233480430312226816.000000
Total training time: 0.02 seconds.
-- Epoch 2
Norm: 1589339362417.63, NNZs: 87, Bias: 1275609435.807366, T: 65018, Avg. loss: 138163229060701241861837160448.000000
Total training time: 0.03 seconds.
-- Epoch 3
Norm: 1871487770343.09, NNZs: 87, Bias: 1384464456.387478, T: 97527, Avg. loss: 105882903593113646849545207808.000000
Total training time: 0.04 seconds.
-- Epoch 4
Norm: 1230822777566.36, NNZs: 87, Bias: 665651092.986896, T: 130036, Avg. loss: 88267879477282046804500676608.000000
Total training time: 0.05 seconds.
-- Epoch 5
Norm: 1604506610018.19, NNZs: 87, Bias: 2322057601.110723, T: 162545, Avg. loss: 77673310825687514072139956224.000000
Total training time: 0.07 seconds.
-- Epoch 6
Norm: 1485716713955.35, NNZs: 87, Bias: 2060856434.643827, T: 195054, Avg. loss: 70987967959361385011523616768.000000
Total training time: 0.08 seconds.
-- Epoch 7
Norm: 1

Norm: 1016013940038.73, NNZs: 87, Bias: -3270046531.915580, T: 2080576, Avg. loss: 20851246578012626292502953984.000000
Total training time: 0.83 seconds.
-- Epoch 65
Norm: 1195536220514.29, NNZs: 87, Bias: -2481497947.442453, T: 2113085, Avg. loss: 20603138048951136013604880384.000000
Total training time: 0.84 seconds.
-- Epoch 66
Norm: 1089332829334.21, NNZs: 87, Bias: -2576213957.364900, T: 2145594, Avg. loss: 20466616719312551556096720896.000000
Total training time: 0.85 seconds.
-- Epoch 67
Norm: 1003263619452.27, NNZs: 87, Bias: -2633550838.144927, T: 2178103, Avg. loss: 20463887635105017933806436352.000000
Total training time: 0.86 seconds.
-- Epoch 68
Norm: 1003965043342.60, NNZs: 87, Bias: -2219433290.974025, T: 2210612, Avg. loss: 20185360792680889573246500864.000000
Total training time: 0.88 seconds.
-- Epoch 69
Norm: 1011638220389.61, NNZs: 87, Bias: -2471825432.664731, T: 2243121, Avg. loss: 20021179352160387267999825920.000000
Total training time: 0.90 seconds.
-- Epoch 7

Norm: 1205159901281.12, NNZs: 87, Bias: -531810828.231790, T: 3933589, Avg. loss: 15155355800460932587857117184.000000
Total training time: 1.64 seconds.
-- Epoch 122
Norm: 1132456226563.28, NNZs: 87, Bias: 30452472.368856, T: 3966098, Avg. loss: 14870447457601835164059566080.000000
Total training time: 1.65 seconds.
-- Epoch 123
Norm: 1178117468608.44, NNZs: 87, Bias: 144860689.371457, T: 3998607, Avg. loss: 14868433832681896666871103488.000000
Total training time: 1.66 seconds.
-- Epoch 124
Norm: 1130283281978.47, NNZs: 87, Bias: -163534413.357256, T: 4031116, Avg. loss: 14806074496177396562127749120.000000
Total training time: 1.68 seconds.
-- Epoch 125
Norm: 1098301221605.46, NNZs: 87, Bias: -58849084.222274, T: 4063625, Avg. loss: 14822417922670224148332019712.000000
Total training time: 1.69 seconds.
-- Epoch 126
Norm: 1158395094608.55, NNZs: 87, Bias: -48468859.625251, T: 4096134, Avg. loss: 14729357676356501966682062848.000000
Total training time: 1.70 seconds.
-- Epoch 127
Nor

Norm: 1160008289871.59, NNZs: 87, Bias: -913154710.957112, T: 5754093, Avg. loss: 12439951043566168683094999040.000000
Total training time: 2.47 seconds.
-- Epoch 178
Norm: 1041235812177.18, NNZs: 87, Bias: -996643341.181321, T: 5786602, Avg. loss: 12449887378214165633182990336.000000
Total training time: 2.48 seconds.
-- Epoch 179
Norm: 1147251829951.79, NNZs: 87, Bias: -853448686.157755, T: 5819111, Avg. loss: 12389616997744952409008898048.000000
Total training time: 2.50 seconds.
-- Epoch 180
Norm: 1128164799702.37, NNZs: 87, Bias: 90919160.634525, T: 5851620, Avg. loss: 12229759180521795900462333952.000000
Total training time: 2.52 seconds.
-- Epoch 181
Norm: 1080924533804.60, NNZs: 87, Bias: -328109332.681252, T: 5884129, Avg. loss: 12305380934165998618261061632.000000
Total training time: 2.53 seconds.
-- Epoch 182
Norm: 1005822280536.30, NNZs: 87, Bias: 15244297.987496, T: 5916638, Avg. loss: 12226654279121988696932352000.000000
Total training time: 2.55 seconds.
-- Epoch 183
No

Norm: 1088721144513.67, NNZs: 87, Bias: -338553170.174318, T: 7444561, Avg. loss: 10829905684459210590304337920.000000
Total training time: 3.51 seconds.
-- Epoch 230
Norm: 1091573598663.84, NNZs: 87, Bias: -303861582.989250, T: 7477070, Avg. loss: 10869110324677880348686680064.000000
Total training time: 3.54 seconds.
-- Epoch 231
Norm: 1139437784735.89, NNZs: 87, Bias: -274289976.989925, T: 7509579, Avg. loss: 10906068123649083231554240512.000000
Total training time: 3.56 seconds.
-- Epoch 232
Norm: 1095444503289.89, NNZs: 87, Bias: -276239948.055220, T: 7542088, Avg. loss: 10839022588243756430800191488.000000
Total training time: 3.58 seconds.
-- Epoch 233
Norm: 1090583039767.78, NNZs: 87, Bias: -214557706.251248, T: 7574597, Avg. loss: 10803945438260387940264837120.000000
Total training time: 3.60 seconds.
-- Epoch 234
Norm: 1058259295833.75, NNZs: 87, Bias: -74998666.415471, T: 7607106, Avg. loss: 10799300365565047748121591808.000000
Total training time: 3.62 seconds.
-- Epoch 235

Norm: 1079223417098.92, NNZs: 87, Bias: -1276066170.798129, T: 9102520, Avg. loss: 9806144808717247020286345216.000000
Total training time: 4.37 seconds.
-- Epoch 281
Norm: 1144225867328.60, NNZs: 87, Bias: -1376887509.656124, T: 9135029, Avg. loss: 9823482291390492820832780288.000000
Total training time: 4.39 seconds.
-- Epoch 282
Norm: 1157721892671.97, NNZs: 87, Bias: -2078232674.683443, T: 9167538, Avg. loss: 9803261541377091905676902400.000000
Total training time: 4.41 seconds.
-- Epoch 283
Norm: 1113072933688.08, NNZs: 87, Bias: -1813565553.034190, T: 9200047, Avg. loss: 9861795810954056939757109248.000000
Total training time: 4.44 seconds.
-- Epoch 284
Norm: 1191100420687.13, NNZs: 87, Bias: -1698175564.540282, T: 9232556, Avg. loss: 9750737251641811201400242176.000000
Total training time: 4.46 seconds.
-- Epoch 285
Norm: 1211196013528.60, NNZs: 87, Bias: -2118877276.300184, T: 9265065, Avg. loss: 9788983419507471428995776512.000000
Total training time: 4.48 seconds.
-- Epoch 28

SGDRegressor(alpha=0.0001, average=False, early_stopping=False, epsilon=0.1,
             eta0=0.01, fit_intercept=True, l1_ratio=0.15,
             learning_rate='invscaling', loss='squared_loss', max_iter=1000,
             n_iter_no_change=5, penalty='l2', power_t=0.25, random_state=None,
             shuffle=True, tol=0.001, validation_fraction=0.1, verbose=True,
             warm_start=False)

In [85]:
y_predsgd = sgd.predict(X_test)
r2_score(y_test, y_predsgd)

-1.0005515487187126e+25

In [86]:
px.line(x=df.timestamp[0:100], y=sgd.predict(X)[0:100], color_discrete_sequence=["darkgreen"])

In [87]:
px.line(x=df.timestamp[0:100], y=sgd.predict(X)[0:100], color_discrete_sequence=["darkgreen"])

In [88]:
px.scatter(x=df.timestamp, y=sgd.predict(X), color_discrete_sequence=["darkgreen"])

#### And finally a Random Forest Regressor

In [89]:
from sklearn.ensemble import RandomForestRegressor

In [90]:
rfr = RandomForestRegressor(verbose=True)

In [91]:
rfr.fit(X_train, y_train)

[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.
[Parallel(n_jobs=1)]: Done 100 out of 100 | elapsed:   51.2s finished


RandomForestRegressor(bootstrap=True, ccp_alpha=0.0, criterion='mse',
                      max_depth=None, max_features='auto', max_leaf_nodes=None,
                      max_samples=None, min_impurity_decrease=0.0,
                      min_impurity_split=None, min_samples_leaf=1,
                      min_samples_split=2, min_weight_fraction_leaf=0.0,
                      n_estimators=100, n_jobs=None, oob_score=False,
                      random_state=None, verbose=True, warm_start=False)

In [92]:
y_predrfr = rfr.predict(X_test)
r2_score(y_test, y_predrfr)

[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.
[Parallel(n_jobs=1)]: Done 100 out of 100 | elapsed:    0.5s finished


0.8395745777082164

In [93]:
df_plot1 = pd.DataFrame(data=rfr.predict(X), index=df.timestamp, columns={'value'})

[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.
[Parallel(n_jobs=1)]: Done 100 out of 100 | elapsed:    1.1s finished


In [94]:
df_plot1['type'] = 'Prediction'

In [95]:
df_plot2 = pd.DataFrame()

In [96]:
df_plot2['value'] = y

In [97]:
df_plot2.index = df.timestamp

In [98]:
df_plot2['type'] = 'Data'

In [99]:
df_plot = pd.concat([df_plot1, df_plot2])

In [100]:
df_plot = df_plot.sort_values('timestamp')

In [101]:
px.line(x=df_plot.index[0:500], y=df_plot.value[0:500], color=df_plot.type[0:500], color_discrete_sequence=["darkgreen", "yellow"]) 

In [102]:
fig = px.line(x=df.timestamp[0:1000], y=rfr.predict(X)[0:1000])

[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.
[Parallel(n_jobs=1)]: Done 100 out of 100 | elapsed:    1.0s finished


In [103]:
fig.add_scatter(x=df.timestamp[0:1000], y=y[0:1000]) # Not what is desired - need a line 

In [104]:
px.bar(y=rfr.feature_importances_, x=df[df.columns[9:]].columns) #Relevanz von Eingangs- auf Ausgangsvariablen - hier auf Ozonwert

In [147]:
rfr_importance = pd.DataFrame()

In [148]:
rfr_importance['column'] = df[df.columns[9:]].columns

In [149]:
rfr_importance['importance'] = rfr.feature_importances_

In [150]:
rfr_importance.sort_values('importance', ascending=False).head()

column  importance
2             temp    0.471306
9       wind_speed    0.085552
10  wind_direction    0.075059
3         humidity    0.061823
4         pressure    0.029476

#### Try some cross validation of the random forest regressor model

In [106]:
from sklearn.model_selection import cross_validate

In [107]:
scores = cross_validate(rfr, X, y, cv=3,
...                         scoring=('r2', 'neg_mean_squared_error'),
...                         return_train_score=True) #Cross Validation vom Random Forest Regression Modell

[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.
[Parallel(n_jobs=1)]: Done 100 out of 100 | elapsed:   41.4s finished
[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.
[Parallel(n_jobs=1)]: Done 100 out of 100 | elapsed:    0.5s finished
[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.
[Parallel(n_jobs=1)]: Done 100 out of 100 | elapsed:    0.8s finished
[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.
[Parallel(n_jobs=1)]: Done 100 out of 100 | elapsed:   41.7s finished
[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.
[Parallel(n_jobs=1)]: Done 100 out of 100 | elapsed:    0.4s finished
[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.
[Parallel(n_jobs=1)]: Done 100 out of 100 | elapsed:    0.7s finished
[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.
[Parallel(n_j

In [108]:
scores

{'fit_time': array([41.46205211, 41.73001671, 43.55787539]),
 'score_time': array([0.47299242, 0.38352776, 0.36687112]),
 'test_r2': array([0.69244932, 0.7028776 , 0.75769274]),
 'train_r2': array([0.9819511 , 0.9816723 , 0.98039548]),
 'test_neg_mean_squared_error': array([-351.96303594, -328.75956821, -321.0290328 ]),
 'train_neg_mean_squared_error': array([-22.07548046, -22.93152393, -22.09926263])}

#### And now the same for the particle < 10 µm data (PM10)

In [109]:
df_PM10_clean = df_all[df_all['PM10'].isna() == False] 

In [110]:
for col in categorical_columns:
    df_PM10_clean[col] = df_all_clean[col].astype('category')

/usr/lib/python3/dist-packages/ipykernel_launcher.py:2: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy



In [111]:
df_PM = pd.get_dummies(df_PM10_clean, drop_first=True)

In [112]:
X_PM = df_PM[df_PM.columns[9:]]

In [113]:
y_PM = df_PM['PM10']

In [114]:
X_PM_train, X_PM_test, y_PM_train, y_PM_test = train_test_split(X_PM, y_PM, test_size=0.33, random_state=42)

In [115]:
rfr2 = RandomForestRegressor(verbose=True)

In [116]:
rfr2.fit(X_PM_train, y_PM_train)

[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.
[Parallel(n_jobs=1)]: Done 100 out of 100 | elapsed:   54.3s finished


RandomForestRegressor(bootstrap=True, ccp_alpha=0.0, criterion='mse',
                      max_depth=None, max_features='auto', max_leaf_nodes=None,
                      max_samples=None, min_impurity_decrease=0.0,
                      min_impurity_split=None, min_samples_leaf=1,
                      min_samples_split=2, min_weight_fraction_leaf=0.0,
                      n_estimators=100, n_jobs=None, oob_score=False,
                      random_state=None, verbose=True, warm_start=False)

In [117]:
y_predrfr_PM = rfr2.predict(X_PM_test)
r2_score(y_PM_test, y_predrfr_PM)

[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.
[Parallel(n_jobs=1)]: Done 100 out of 100 | elapsed:    0.6s finished


0.6912835026540087

In [118]:
fig2 = px.line(x=df_PM.timestamp[0:1000], y=rfr2.predict(X_PM)[0:1000])

[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.
[Parallel(n_jobs=1)]: Done 100 out of 100 | elapsed:    1.1s finished


In [119]:
fig2.add_scatter(x=df_PM.timestamp[0:1000], y=y_PM[0:1000]) # Not what is desired - need a line 

In [120]:
rfr2.feature_importances_.shape

(87,)

In [121]:
df_PM[df_PM.columns[9:]].columns

Index(['TrafficIn', 'TrafficOut', 'temp', 'humidity', 'pressure',
       'precipitation', 'cloudcover', 'sunshine_duration',
       'shortwave_radiation', 'wind_speed', 'wind_direction', 'hour_1',
       'hour_2', 'hour_3', 'hour_4', 'hour_5', 'hour_6', 'hour_7', 'hour_8',
       'hour_9', 'hour_10', 'hour_11', 'hour_12', 'hour_13', 'hour_14',
       'hour_15', 'hour_16', 'hour_17', 'hour_18', 'hour_19', 'hour_20',
       'hour_21', 'hour_22', 'hour_23', 'weekday_1', 'weekday_2', 'weekday_3',
       'weekday_4', 'weekday_5', 'weekday_6', 'month_2', 'month_3', 'month_4',
       'month_5', 'month_6', 'month_7', 'month_8', 'month_9', 'month_10',
       'month_11', 'month_12', 'year_2015', 'year_2016', 'year_2017',
       'year_2018', 'year_2019', 'year_2020', 'day_2', 'day_3', 'day_4',
       'day_5', 'day_6', 'day_7', 'day_8', 'day_9', 'day_10', 'day_11',
       'day_12', 'day_13', 'day_14', 'day_15', 'day_16', 'day_17', 'day_18',
       'day_19', 'day_20', 'day_21', 'day_22', 'day_23', 

In [127]:
px.bar(y=rfr2.feature_importances_, x=df_PM[df_PM.columns[9:]].columns, color_discrete_sequence=["darkgreen"])

In [137]:
rfr2_importance = pd.DataFrame()

In [140]:
rfr2_importance['column'] = df_PM[df_PM.columns[9:]].columns

In [141]:
rfr2_importance['importance'] = rfr2.feature_importances_

In [145]:
rfr2_importance.sort_values('importance', ascending=False).head()

importance          column
2     0.155524            temp
10    0.114143  wind_direction
9     0.106946      wind_speed
4     0.092128        pressure
3     0.046423        humidity

In [ ]:
#